# Lions Bay Data Logger Processing
Code to import data logger data, view and analyze. HOBOWare software was used to apply the barometric pressure correction to the corrected input files.

## Import Libraries

In [1]:
import math
import pandas as pd
import numpy as np
from scipy import stats as st
import datetime

import matplotlib.pyplot as plt
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()

from bokeh.plotting import figure, show, output_file
from bokeh.models import ColumnDataSource, Band, LinearAxis, Range1d
from bokeh.io import output_notebook
from bokeh.layouts import gridplot
output_notebook()

Loading BokehJS ...

## Import Data

In [2]:
stage_df = pd.read_csv('water_level_data_LB/10174477_pressure_comp.csv',header=1)
stage_df = stage_df.drop(columns=['#'])
stage_df['Date Time, GMT-07:00'] = pd.to_datetime(stage_df['Date Time, GMT-07:00'],yearfirst=True)

#stage_df

In [3]:
intake_df = pd.read_csv('water_level_data_LB/Harvey_Reservoir-Magnesia_Reservoir_export.csv', header=2)
# stage_df = stage_df.drop(columns=['#'])
intake_df['yyyy/MM/dd hh:mm:ss'] = pd.to_datetime(intake_df['yyyy/MM/dd hh:mm:ss'],yearfirst=True)

intake_df

yyyy/MM/dd hh:mm:ss  HARV_PRV_FLOW (gpm)  MAG_PRV_FLOW (gpm)
0      2020-07-24 00:00:00                  0.1                 0.3
1      2020-07-24 00:00:07                  0.1                 0.3
2      2020-07-24 00:00:22                  0.1                 0.3
3      2020-07-24 00:00:37                  0.1                 0.8
4      2020-07-24 00:00:52                  0.1                 0.0
...                    ...                  ...                 ...
386645 2020-10-01 22:59:08                  0.1                 0.0
386646 2020-10-01 22:59:23                  0.1                 0.0
386647 2020-10-01 22:59:38                  0.1                 0.0
386648 2020-10-01 22:59:53                  0.1                 0.0
386649 2020-10-01 23:00:00                  0.1                 0.0

[386650 rows x 3 columns]

## Plot Data

In [4]:
# customize the tools for interacting with the bokeh plot
TOOLS="pan,wheel_zoom,reset,hover,poly_select,box_select"

daily_flow_plot = figure(plot_width=500, plot_height=300, 
                        x_axis_type='datetime', title='Water Level', y_range=(0, 0.1))

# plot the daily flow series generated from the rating curve
# daily_flow_plot.circle(intake_df['yyyy/MM/dd hh:mm:ss'], intake_df['HARV_PRV_FLOW (gpm)'], size=1, color="red", alpha=0.5)
daily_flow_plot.line(stage_df['Date Time, GMT-07:00'], stage_df['Sensor Depth, meters (LGR S/N: 10174477)'], color='green')
daily_flow_plot.circle(intake_df['yyyy/MM/dd hh:mm:ss'], intake_df['HARV_PRV_FLOW (gpm)'], size=1, color="red", alpha=0.5, y_range_name='foo',)

# label the axes
daily_flow_plot.extra_y_ranges = {"foo": Range1d(start=0, end=1000)}
daily_flow_plot.xaxis.axis_label = 'Date'
daily_flow_plot.yaxis.axis_label = 'Depth (m)'

#rc_plot.legend.location = "bottom_right"

layout = gridplot([[daily_flow_plot]])
daily_flow_plot.add_layout(LinearAxis(y_range_name="foo", axis_label='Intake Flowrate (gpm)'), 'right')

# show the results
show(layout)

## Establish Diurnal Cycle

sample code from: https://www.davidhagan.me/articles?id=7

In [5]:
stage_df['Time'] = stage_df['Date Time, GMT-07:00'].map(lambda x: x.strftime("%H:%M"))

stage_df_stats = stage_df.groupby('Time').describe().unstack()

stage_df

Date Time, GMT-07:00  \
0     2020-07-24 12:45:49   
1     2020-07-24 12:45:57   
2     2020-07-24 13:00:00   
3     2020-07-24 13:00:49   
4     2020-07-24 13:15:49   
...                   ...   
9943  2020-10-01 13:45:49   
9944  2020-10-01 14:00:00   
9945  2020-10-01 14:00:40   
9946  2020-10-01 14:00:44   
9947  2020-10-01 14:00:49   

      Abs Pres, kPa (LGR S/N: 10174477, SEN S/N: 10174477)  \
0                                                97.956      
1                                                   NaN      
2                                                   NaN      
3                                                98.595      
4                                                98.607      
...                                                 ...      
9943                                             99.039      
9944                                                NaN      
9945                                                NaN      
9946                                                NaN      
9947                                             98.798      

      Temp, °C (LGR S/N: 10174477, SEN S/N: 10174477)  \
0                                              17.855   
1                                                 NaN   
2                                                 NaN   
3                                              11.139   
4                                              11.139   
...                                               ...   
9943                                           12.207   
9944                                              NaN   
9945                                              NaN   
9946                                              NaN   
9947                                           15.187   

      Abs Pres Barom., kPa (LGR S/N: 10246300, SEN S/N: 10246300)  \
0                                                   NaN             
1                                                   NaN             
2                                                98.136             
3                                                   NaN             
4                                                   NaN             
...                                                 ...             
9943                                                NaN             
9944                                             98.465             
9945                                                NaN             
9946                                                NaN             
9947                                                NaN             

      Sensor Depth, meters (LGR S/N: 10174477)  \
0                                       -0.018   
1                                          NaN   
2                                          NaN   
3                                        0.047   
4                                        0.055   
...                                        ...   
9943                                     0.057   
9944                                       NaN   
9945                                       NaN   
9946                                       NaN   
9947                                     0.034   

     Coupler Detached (LGR S/N: 10174477)  \
0                                     NaN   
1                                  Logged   
2                                     NaN   
3                                     NaN   
4                                     NaN   
...                                   ...   
9943                                  NaN   
9944                                  NaN   
9945                                  NaN   
9946                                  NaN   
9947                                  NaN   

     Coupler Attached (LGR S/N: 10174477) Host Connected (LGR S/N: 10174477)  \
0                                     NaN                                NaN   
1                                     NaN                                NaN   
2              

In [6]:
#time = stage_df['Time']

# time = pd.to_datetime(['00:00', '00:15', '00:30', '00:45', '01:00', '01:15', '01:30', '01:45',
#       '02:00', '02:15', '02:30', '02:45', '03:00', '03:15', '03:30', '03:45',
#       '04:00', '04:15', '04:30', '04:45', '05:00', '05:15', '05:30', '05:45',
#       '06:00', '06:15', '06:30', '06:45', '07:00', '07:15', '07:30', '07:45',
#       '08:00', '08:15', '08:30', '08:45', '09:00', '09:15', '09:30', '09:45',
#       '10:00', '10:15', '10:30', '10:45', '11:00', '11:15', '11:30', '11:45',
#       '12:00', '12:15', '12:30', '12:45', '13:00', '13:15', '13:30', '13:45',
#       '14:00', '14:15', '14:30', '14:45', '15:00', '15:15', '15:30', '15:45',
#       '16:00', '16:15', '16:30', '16:45', '17:00', '17:15', '17:30', '17:45',
#       '18:00', '18:15', '18:30', '18:45', '19:00', '19:15', '19:30', '19:45',
#       '20:00', '20:15', '20:30', '20:45', '21:00', '21:15', '21:30', '21:45',
#       '22:00', '22:15', '22:30', '22:45', '23:00', '23:15', '23:30', '23:45'])

mean = stage_df_stats['Sensor Depth, meters (LGR S/N: 10174477)']['mean']

time = pd.to_datetime(stage_df_stats['Sensor Depth, meters (LGR S/N: 10174477)']['mean'].index)

In [7]:
# customize the tools for interacting with the bokeh plot
TOOLS="pan,wheel_zoom,reset,hover,poly_select,box_select"

diurnal_level_plot = figure(plot_width=500, plot_height=300, 
                        x_axis_type='datetime', title='Mean Diurnal Water Level', y_range=(0, 0.1))

# plot the daily flow series generated from the rating curve
diurnal_level_plot.line(time, mean, color='green')

# label the axes
diurnal_level_plot.xaxis.axis_label = 'Date'
diurnal_level_plot.yaxis.axis_label = 'Depth (m)'

layout = gridplot([[diurnal_level_plot]])

# show the results
show(layout)

## Phase & Water Level Plots

Collaborated with Dan to generate the following code. Simultaneous linked plots showing difference in depth against water level (showing locations of maximum water level changing). When selecting data on either plot, the points are highlighted on the other.

In [8]:
depth = 'Sensor Depth, meters (LGR S/N: 10174477)'
date = 'Date Time, GMT-07:00'
# print(stage_df[[depth, date]].head())

df = stage_df[[depth, date]].copy()
df.dropna(inplace=True)
df['Date'] = pd.to_datetime(df[date].apply(lambda x: x.strftime('%Y-%m-%d')))
df.set_index(date, inplace=True)
df['hour'] = df.index.hour
df['d_depth'] = df[depth].diff()
# df.reset_index(inplace=True)

df

Sensor Depth, meters (LGR S/N: 10174477)       Date  \
Date Time, GMT-07:00                                                        
2020-07-24 12:45:49                                     -0.018 2020-07-24   
2020-07-24 13:00:49                                      0.047 2020-07-24   
2020-07-24 13:15:49                                      0.055 2020-07-24   
2020-07-24 13:30:49                                      0.059 2020-07-24   
2020-07-24 13:45:49                                      0.057 2020-07-24   
...                                                        ...        ...   
2020-10-01 13:00:49                                      0.058 2020-10-01   
2020-10-01 13:15:49                                      0.058 2020-10-01   
2020-10-01 13:30:49                                      0.057 2020-10-01   
2020-10-01 13:45:49                                      0.057 2020-10-01   
2020-10-01 14:00:49                                      0.034 2020-10-01   

                      hour  d_depth  
Date Time, GMT-07:00                 
2020-07-24 12:45:49     12      NaN  
2020-07-24 13:00:49     13    0.065  
2020-07-24 13:15:49     13    0.008  
2020-07-24 13:30:49     13    0.004  
2020-07-24 13:45:49     13   -0.002  
...                    ...      ...  
2020-10-01 13:00:49     13   -0.002  
2020-10-01 13:15:49     13    0.000  
2020-10-01 13:30:49     13   -0.001  
2020-10-01 13:45:49     13    0.000  
2020-10-01 14:00:49     14   -0.023  

[6630 rows x 4 columns]

In [9]:
all_dates = list(set(df['Date'].values))

TOOLS="pan,wheel_zoom,reset,hover,poly_select,box_select"

diurnal_level_plot = figure(plot_width=600, plot_height=300, tools=TOOLS,
                        title='Mean Diurnal Water Level', x_axis_type='datetime')

phase_plot = figure(plot_width=400, plot_height=300, tools=TOOLS,
                        title='Phase')

# plot the daily flow series generated from the rating curve
# diurnal_level_plot.line(time, mean, color='green')

from bokeh.layouts import gridplot
from bokeh.models import ColumnDataSource

source = ColumnDataSource(df)

In [10]:
from bokeh.models import Circle
# alpha = 0.1
for d in all_dates:
    data = df[df['Date'] == d]
    diurnal_level_plot.circle(data.index, data[depth])
    

p1 = diurnal_level_plot.circle(date, depth, source=source)
p2 = phase_plot.circle(depth, 'd_depth',source=source)

selected_circle = Circle(fill_alpha=1, fill_color="firebrick", line_color=None)
p1.selection_glyph = selected_circle
p2.selection_glyph = selected_circle

p = gridplot([[diurnal_level_plot, phase_plot]])
# p.selection_glyph = Circle(fill_color="orange", line_color=None)
# p.nonselection_glyph = Circle(fill_color="black", line_color=None)
    
show(p)

## Establish Diurnal Cycle

Collaborated with Dan to generate the following code. 

Need to make the colour bar thing work so that lines change color as day increases. 

In [14]:
hourly_data = {'median': [],
              'low': [],
              'high': [],
              'hour': list(range(24))}
for h in range(24):
    data = df.loc[df['hour'] == h, depth].to_numpy()
    hourly_data['median'].append(np.percentile(data, 50))
    hourly_data['low'].append(np.percentile(data, 5))
    hourly_data['high'].append(np.percentile(data, 95))

band_df = pd.DataFrame(hourly_data)
band_source = ColumnDataSource(band_df)

start = df.index[0].strftime('%Y-%m-%d')
end = df.index[-1].strftime('%Y-%m-%d')
p = figure(plot_width=700, plot_height=300, 
                            title='Diurnal Water Level ({} to {})'.format(start, end),
          y_range=(band_df['low'].min(), band_df['high'].max()))

p.line('hour', 'median', source=band_source, color='blue', line_dash='dashed',legend='Median of Data')
p.varea(x='hour', y1='low', y2='high', source=band_source,
        fill_alpha=0.5, fill_color='mediumseagreen', legend='2 sigma bounds')

band = Band(base='median', lower='low', upper='high', source=band_source, level='underlay')

p.add_layout(band)
p.yaxis.axis_label = depth
p.xaxis.axis_label = 'Hour of the day'
show(p)